# Foundations

### Convert to base 2

In [1]:
def convert(x):
    if x == 0: return "0"
    if x == 1: return "1"
    return convert(x//2) + convert(x%2)

convert(34)

'100010'

### Collatz sequence

In [2]:
def collatz(n):
    print(n, " ", end="")
    
    if n == 1: 
        return
    
    if n % 2 == 0: 
        collatz(n // 2)
        return
    
    collatz(3*n + 1)
    
collatz(7)


7  22  11  34  17  52  26  13  40  20  10  5  16  8  4  2  1  

# Classic example

### Subdivisions of a ruller

In [3]:
def ruler(n):
    if n==0: return " "
    return ruler(n-1) + str(n) + ruler(n-1)        
    
ruler(4)

' 1 2 1 3 1 2 1 4 1 2 1 3 1 2 1 '

### Towers of Hanoi

In [4]:
def reverse(direction):
    if direction=="L": return "R"
    if direction=="R": return "L"
    raise Exception("unknown direction: " + direction)

def hanoi(n, direction):
    """
    Assumes that we have one sorted pile of disks with largest disk size n on the middle spindle.
    The returned instruction describes how disks with different sizes must be moved so that the whole sorted pile
    would relocate in the specified direction. Moves are cyclic, L means Left, R means Right. Cyclic means that 
    if we move leftmost to the left it would cycle through to the rightmost position, simialr for other direction.
    """
    if n==0: return " "
    moveSmallerPileAway = hanoi(n-1, reverse(direction))
    moveLargeDisk = str(n) + direction
    moveSmallerPileOnTop = hanoi(n-1, reverse(direction))
    return moveSmallerPileAway + moveLargeDisk + moveSmallerPileOnTop
    

In [5]:
hanoi(4, "L")

' 1R 2L 1R 3R 1R 2L 1R 4L 1R 2L 1R 3R 1R 2L 1R '

Disk 1 always moves right. Disk 2 always moves left. The same for all other disk sizes - they move only in one direction. And if we always move the smallest disk to the right, there is only one possible move available on the other two disks since we can't put anything on top of the smallest disk. This is the algorithm that can be explained to a human. And this algorithm would work without needing lots of stack and that would cover any n.

And the compute complexity is 2\*\*N - 1. For the profecy time estimate we need to check n for 64. And mutiply by the time it takes to move the disk. Let's assume it is one minute.

In [6]:
operations = 2**64 - 1
inSeconds = operations * 60
inCenturies = inSeconds / 60 / 60 / 24 / 365 / 100
inCenturies

350965450413.0432

# Recursive graphics

## H space filling curve

Solves problems like attaching electric source to a lot of sites: electrical wiring for a city, electric curcuit chips. Gives connection to everywhere in an organized fashion.

In [7]:
from math import sqrt
import plotly.graph_objects as go
from plotly.graph_objects import Figure as figure
from plotly.graph_objects import Scatter as scatter

In [8]:
def construct(length = 1.0, x0 = 0.0, y0 = 0.0):
    delta = length / 2.0

    # Left vertical
    x1 = [x0 - delta, x0 - delta]
    y1 = [y0 - delta, y0 + delta]

    # Horizontal line
    x2 = [x0 - delta, x0 + delta]
    y2 = [y0, y0]

    # Right vertical
    x3 = [x0 + delta, x0 + delta]
    y3 = [y0 - delta, y0 + delta]
    
    # Combining all together
    x = x1 + [None] + x2 + [None] + x3
    y = y1 + [None] + y2 + [None] + y3
    return x, y

def corners(length = 1.0, x0 = 0.0, y0 = 0.0):
    delta = length / 2.0
    x = [x0 - delta, x0 - delta, x0 + delta, x0 + delta]
    y = [y0 - delta, y0 + delta, y0 - delta, y0 + delta]
    return x, y

def recursive_construct(length = 1.0, x0 = 0.0, y0 = 0.0, n = 0):
    if n==0: return [], []
    
    xc, yc = corners(length, x0, y0)
    x1, y1 = recursive_construct(length / 2.0, xc[0], yc[0], n-1)
    x2, y2 = recursive_construct(length / 2.0, xc[1], yc[1], n-1)
    x3, y3 = recursive_construct(length / 2.0, xc[2], yc[2], n-1)
    x4, y4 = recursive_construct(length / 2.0, xc[3], yc[3], n-1)

    x,y = construct(length, x0, y0)
    x = x + [None] + x1 + [None] + x2 + [None] + x3 + [None] + x4
    y = y + [None] + y1 + [None] + y2 + [None] + y3 + [None] + y4
        
    return x, y

def draw(x, y):   
    f = figure(
        scatter(
            x = x,
            y = y,
        ),
        layout = {
            "template": "plotly_white",
            "yaxis": {"scaleanchor": "x", "scaleratio": 1},
        },  
    )
    f.show()
    
x,y = recursive_construct(length = 1.0, x0 = 0.0, y0 = 0.0, n = 6)
draw(x,y)


In [9]:
def make_h(d=0.5, x=0, y=0):
    return [
        (x-d, y-d, x-d, y+d),
        (x-d, y+0, x+d, y+0),
        (x+d, y-d, x+d, y+d),
    ]


def make_h_recurse(n, sz = 1, x = 0, y = 0):
    if n <= 0: raise ValueError

    d = sz / 2  
    result = make_h(d, x, y)

    if n > 1:
        result += make_h_recurse(n-1, d, x-d, y-d)
        result += make_h_recurse(n-1, d, x-d, y+d)
        result += make_h_recurse(n-1, d, x+d, y-d)
        result += make_h_recurse(n-1, d, x+d, y+d)

    return result


def convert_lines_to_xy(lines):
    "lines is array of tuples (x0, y0, x1, y1)"
    x_lines = [[line[0], line[2], None] for line in lines]
    y_lines = [[line[1], line[3], None] for line in lines]
    x = [x for x_line in x_lines for x in x_line]
    y = [y for y_line in y_lines for y in y_line]
    return x[:-1], y[:-1]
    

def draw(lines):    
    x, y = convert_lines_to_xy(lines)
    figure(
        scatter(x = x, y = y),
        layout = {
            "template": "plotly_white",
            "yaxis": {"scaleanchor": "x", "scaleratio": 1},
        },  
    ).show()   

    
lines = make_h_recurse(4)
draw(lines)


## Fractional Brownian motion

Actual name of it is *midpoint displacement method*. Can be used as a model for:
- stock prices
- dispersion iof fluids
- shapes of mointains and clouds

In [10]:
from random import gauss
import plotly.graph_objects as go
from plotly.graph_objects import Figure as figure
from plotly.graph_objects import Scatter as scatter 

In [11]:
def brownian_middle(x0, y0, x1, y1, mu = 0, sigma = 1):
    xm = (x0 + x1) / 2
    ym = (y0 + y1) / 2
    d = gauss(mu, sigma)
    return xm, ym + d

def midpoint_displacement(x0, y0, x1, y1, mu = 0, sigma = 1, n = 0):
    if n==0: return [], []

    xm, ym = brownian_middle(x0, y0, x1, y1, mu, sigma)

    if n==1:
        x = [x0, xm, x1]
        y = [y0, ym, y1]
        return x, y

    xl, yl = midpoint_displacement(x0, y0, xm, ym, mu, sigma, n - 1)
    xr, yr = midpoint_displacement(xm, ym, x1, y1, mu, sigma, n - 1)
    x = xl + xr[1:]
    y = yl + yr[1:]
    return x, y
    
print(brownian_middle(0,0, 1,0))
print(midpoint_displacement(0,0, 1,0, n=3))

(0.5, -0.3610203119407617)
([0, 0.125, 0.25, 0.375, 0.5, 0.625, 0.75, 0.875, 1], [0, 0.9487540259839626, -1.440001851474796, -1.7077656468120397, -0.5982546536256463, 0.6695166452305897, -1.3692679017259877, 0.31388859711259287, 0])


In [12]:
def draw(x, y):   
    f = figure(
        scatter(
            x = x,
            y = y,
        ),
        layout = {
            "template": "plotly_white",
        },  
    )
    f.show()

In [13]:
x,y = midpoint_displacement(0,0, 1,1, 0, 1, n=10)
draw(x,y)

# Plasma clouds

- Point: x, y, color - 0 means black, 100 means white.
- Rectangle: 4 points.
- Pre allocated matrix of points to save space. x, y are replaced by indexes.

In [14]:
from random import gauss
import plotly.graph_objects as go
from plotly.graph_objects import Figure as figure
from plotly.graph_objects import Heatmap as heatmap 

In [15]:
def allocate_matrix(x_pow, y_pow, lu_color = 0, ru_color = 20, ld_color = 60, rd_color = 100):
    w = 2 ** x_pow
    h = 2 ** y_pow
    
    matrix = [[0] * (w+1) for _ in range(h+1)]
    
    matrix[0][0] = lu_color
    matrix[0][w] = ru_color
    matrix[h][0] = ld_color
    matrix[h][w] = rd_color
    
    return matrix

def solve_matrix(m, xs, ys, xe, ye, mu = 0, sigma = 1):
    x_defined = (xe + xs) % 2 == 0 and xs < xe
    y_defined = (ye + ys) % 2 == 0 and ys < ye
    
    if x_defined:
        x = (xe + xs) // 2
        m[ys][x] = (m[ys][xs] + m[ys][xe]) / 2
        m[ye][x] = (m[ye][xs] + m[ye][xe]) / 2
    
    if y_defined:
        y = (ye + ys) // 2
        m[y][xs] = (m[ys][xs] + m[ye][xs]) / 2
        m[y][xe] = (m[ys][xe] + m[ye][xe]) / 2
        
    if x_defined and y_defined:
        d = gauss(mu, sigma)
        m[y][x] = (m[ys][x] + m[ye][x] + m[y][xs] + m[y][xe]) / 4 + d
        
    return x_defined or y_defined

def solve_recurse(m, xs, ys, xe, ye, mu = 0, sigma = 1):
    go_deeper = solve_matrix(m, xs, ys, xe, ye, mu, sigma)

    if go_deeper:
        x = (xe + xs) // 2
        y = (ye + ys) // 2
        solve_recurse(m, xs, ys, x, y, mu, sigma)
        solve_recurse(m, x, y, xe, ye, mu, sigma)
        solve_recurse(m, x, ys, xe, y, mu, sigma)
        solve_recurse(m, xs, y, x, ye, mu, sigma)
        
xp = 8
yp = 8
m = allocate_matrix(xp, yp, 0, 60 ,10, 100)
solve_recurse(m, 0, 0, 2**xp, 2**yp, mu = 0, sigma = 4)

figure(
    heatmap(
        z = m,
        colorscale=[
            [0.0, "rgb(50,50,255)"],
            [1.0, "rgb(255,255,255)"]]
    ),
    layout = {
        "template": "plotly_white",
        "xaxis": {"visible": False},
        "yaxis": {"visible": False, "scaleanchor": "x", "scaleratio": 1},
    }
)

# Fibonachi numbers

Can be used to study rabbit populations. Describes nautilus shells.

In [16]:
from functools import lru_cache

@lru_cache(maxsize=None)
def fib(n):
    if n == 0: return 0
    if n == 1: return 1
    return fib(n-1) + fib(n-2)

print([fib(n) for n in range(0, 60)])
print(fib.cache_info())

[0, 1, 1, 2, 3, 5, 8, 13, 21, 34, 55, 89, 144, 233, 377, 610, 987, 1597, 2584, 4181, 6765, 10946, 17711, 28657, 46368, 75025, 121393, 196418, 317811, 514229, 832040, 1346269, 2178309, 3524578, 5702887, 9227465, 14930352, 24157817, 39088169, 63245986, 102334155, 165580141, 267914296, 433494437, 701408733, 1134903170, 1836311903, 2971215073, 4807526976, 7778742049, 12586269025, 20365011074, 32951280099, 53316291173, 86267571272, 139583862445, 225851433717, 365435296162, 591286729879, 956722026041]
CacheInfo(hits=116, misses=60, maxsize=None, currsize=60)


# Dynamic programming

Solve problem bottom-up. First solve small problems, then use known soltions to small problems o handle bigger problems.

In [17]:
fib = [0] * 100
fib[0] = 0
fib[1] = 1
for i in range(2,100):
    fib[i] = fib[i-1] + fib[i-2]
print(fib)

[0, 1, 1, 2, 3, 5, 8, 13, 21, 34, 55, 89, 144, 233, 377, 610, 987, 1597, 2584, 4181, 6765, 10946, 17711, 28657, 46368, 75025, 121393, 196418, 317811, 514229, 832040, 1346269, 2178309, 3524578, 5702887, 9227465, 14930352, 24157817, 39088169, 63245986, 102334155, 165580141, 267914296, 433494437, 701408733, 1134903170, 1836311903, 2971215073, 4807526976, 7778742049, 12586269025, 20365011074, 32951280099, 53316291173, 86267571272, 139583862445, 225851433717, 365435296162, 591286729879, 956722026041, 1548008755920, 2504730781961, 4052739537881, 6557470319842, 10610209857723, 17167680177565, 27777890035288, 44945570212853, 72723460248141, 117669030460994, 190392490709135, 308061521170129, 498454011879264, 806515533049393, 1304969544928657, 2111485077978050, 3416454622906707, 5527939700884757, 8944394323791464, 14472334024676221, 23416728348467685, 37889062373143906, 61305790721611591, 99194853094755497, 160500643816367088, 259695496911122585, 420196140727489673, 679891637638612258, 110008777

## Longest common subsequence length

Subsequence is any string that we get after deleting any number of chars from the original string

In [57]:
def lcs(s, t):
    m = len(s) # m, s, i, width
    n = len(t) # n, t, j, height
    width = m + 1
    height = n + 1
    opt = [[0] * width for _ in range(height)]

    for j in range(n,-1,-1):
        for i in range(m,-1,-1):
            if i == m or j == n: 
                opt[j][i] = 0
            elif s[i] == t[j]: 
                opt[j][i] = opt[j+1][i+1] + 1
            else:
                opt[j][i] = max(opt[j][i+1], opt[j+1][i])

    return opt[0][0]

lcs("acggcggatacg", "ggcaccacg")

7